#0. Set Up

In [1]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [2]:
%cd "drive/Othercomputers/내 노트북/Forked_Models/Yolov7_StrongSORT_OSNet"

/content/drive/Othercomputers/내 노트북/Forked_Models/Yolov7_StrongSORT_OSNet


In [3]:
%pip install -qr requirements.txt  # install dependencies
import tensorflow as tf
import torch
from IPython.display import Image, clear_output  # to display images

clear_output()
print(f"Setup complete. Using torch {torch.__version__} ({torch.cuda.get_device_properties(0).name if torch.cuda.is_available() else 'CPU'})")

Setup complete. Using torch 2.0.0+cu118 (CPU)


In [4]:
# get yolov5m model trained on the crowd-human dataset
!wget -nc https://github.com/WongKinYiu/yolov7/releases/download/v0.1/yolov7.pt -O "/content/drive/Othercomputers/내 노트북/Forked_Models/Yolov7_StrongSORT_OSNet/yolov7.pt"

# get the test video from the repo
#!wget -nc https://github.com/mikel-brostrom/Yolov5_StrongSORT_OSNet/releases/download/v.2.0/test.avi
# extract 3 seconds worth of video frames of it
#!yes | ffmpeg -ss 00:00:00 -i test.avi -t 00:00:02 -c copy out.avi

File ‘/content/drive/Othercomputers/내 노트북/Forked_Models/Yolov7_StrongSORT_OSNet/yolov7.pt’ already there; not retrieving.


#1. Object Tracking + Pose Estimation

## Test

In [5]:
import argparse

import os
# limit the number of cpus used by high performance libraries
os.environ["OMP_NUM_THREADS"] = "1"
os.environ["OPENBLAS_NUM_THREADS"] = "1"
os.environ["MKL_NUM_THREADS"] = "1"
os.environ["VECLIB_MAXIMUM_THREADS"] = "1"
os.environ["NUMEXPR_NUM_THREADS"] = "1"

import pathlib
import sys
import numpy as np
from pathlib import Path
import torch
import torch.backends.cudnn as cudnn
from numpy import random

#FILE = "/content/drive/Othercomputers/내 노트북/Forked_Models/Yolov7_StrongSORT_OSNet"
#FILE = Path(__file__).resolve()
ROOT = "/content/drive/Othercomputers/내 노트북/Forked_Models/Yolov7_StrongSORT_OSNet"
#ROOT = FILE.parents[0]  # yolov5 strongsort root directory
WEIGHTS = "/content/drive/Othercomputers/내 노트북/Forked_Models/Yolov7_StrongSORT_OSNet/weights"
#WEIGHTS = ROOT/ 'weights'


if str(ROOT) not in sys.path:
    sys.path.append(str(ROOT))  # add ROOT to PATH
if str(ROOT + '/yolov7') not in sys.path:
    sys.path.append(str(ROOT + '/yolov7'))  # add yolov5 ROOT to PATH
if str(ROOT + '/strong_sort') not in sys.path:
    sys.path.append(str(ROOT + '/strong_sort'))  # add strong_sort ROOT to PATH
ROOT = Path(os.path.relpath(ROOT, Path.cwd()))  # relative


from yolov7.models.experimental import attempt_load
from yolov7.utils.datasets import LoadImages, LoadStreams
from yolov7.utils.general import (check_img_size, non_max_suppression, scale_coords, check_requirements, cv2,
                                  check_imshow, xyxy2xywh, increment_path, strip_optimizer, colorstr, check_file)
from yolov7.utils.torch_utils import select_device, time_synchronized
from yolov7.utils.plots import plot_one_box
from strong_sort.utils.parser import get_config
from strong_sort.strong_sort import StrongSORT

from yolov7.utils.datasets import letterbox
from yolov7.utils.general import non_max_suppression_kpt
from yolov7.utils.plots import output_to_keypoint, plot_skeleton_kpts,plot_one_box_kpt

VID_FORMATS = 'asf', 'avi', 'gif', 'm4v', 'mkv', 'mov', 'mp4', 'mpeg', 'mpg', 'ts', 'wmv'  # include video suffixes

/content/drive/Othercomputers/내 노트북/Forked_Models/Yolov7_StrongSORT_OSNet/strong_sort/deep/reid/torchreid/metrics/rank.py:11: UserWarning: Cython evaluation (very fast so highly recommended) is unavailable, now use python evaluation.
  warnings.warn(


In [6]:
@torch.no_grad()
def run(
        source='/content/drive/Othercomputers/내 노트북/Forked_Models/Data_A/Image_A',
        yolo_weights= 'yolov5m.pt',  # model.pt path(s),
        strong_sort_weights='osnet_x0_25_msmt17.pt',  # model.pt path,
        config_strongsort='/content/drive/Othercomputers/내 노트북/Forked_Models/Yolov7_StrongSORT_OSNet/strong_sort/configs/strong_sort.yaml',
        imgsz=(1080, 1920),  # inference size (height, width)
        conf_thres=0.15,  # confidence threshold
        iou_thres=0.45,  # NMS IOU threshold
        max_det=1000,  # maximum detections per image
        device=0,  # cuda device, i.e. 0 or 0,1,2,3 or cpu
        show_vid=False,  # show results
        save_txt=False,  # save results to *.txt
        save_conf=False,  # save confidences in --save-txt labels
        save_crop=False,  # save cropped prediction boxes
        save_vid=False,  # save confidences in --save-txt labels
        nosave=False,  # do not save images/videos
        classes=0,  # filter by class: --class 0, or --class 0 2 3
        agnostic_nms=False,  # class-agnostic NMS
        augment=False,  # augmented inference
        visualize=False,  # visualize features
        update=False,  # update all models
        project='/content/drive/Othercomputers/내 노트북/Forked_Models/Yolov7_StrongSORT_OSNet/runs/track',  # save results to project/name
        name='exp',  # save results to project/name
        exist_ok=False,  # existing project/name ok, do not increment
        line_thickness=3,  # bounding box thickness (pixels)
        hide_labels=False,  # hide labels
        hide_conf=False,  # hide confidences
        hide_class=False,  # hide IDs
        half=False,  # use FP16 half-precision inference
        dnn=False,  # use OpenCV DNN for ONNX inference
):
    det_list = []
    source = str(source)
    save_img = not nosave and not source.endswith('.txt')  # save inference images
    is_file = Path(source).suffix[1:] in (VID_FORMATS)
    is_url = source.lower().startswith(('rtsp://', 'rtmp://', 'http://', 'https://'))
    webcam = source.isnumeric() or source.endswith('.txt') or (is_url and not is_file)
    if is_url and is_file:
        source = check_file(source)  # download

    # Directories
    if not isinstance(yolo_weights, list):  # single yolo model
        exp_name = pathlib.Path(yolo_weights).stem
    elif type(yolo_weights) is list and len(yolo_weights) == 1:  # single models after --yolo_weights
        exp_name = pathlib.Path(yolo_weights[0]).stem
        yolo_weights = Path(yolo_weights[0])
    else:  # multiple models after --yolo_weights
        exp_name = 'ensemble'
    exp_name = name if name else exp_name + "_" + strong_sort_weights.stem
    save_dir = increment_path(Path(project) / exp_name, exist_ok=exist_ok)  # increment run
    save_dir = Path(save_dir)
    (save_dir + '/tracks' if save_txt else save_dir).mkdir(parents=True, exist_ok=True)  # make dir

    # Load model
    device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
    print(device)

    pathlib.Path(WEIGHTS).mkdir(parents=True, exist_ok=True)
    model = loading_yolov7_model(Path("/content/drive/Othercomputers/내 노트북/Forked_Models/Yolov7_StrongSORT_OSNet/yolov7/yolov7-w6-pose.pt"), device)  # load FP32 model
    names, = model.names,
    stride = model.stride.max().cpu().numpy()  # model stride
    imgsz = check_img_size(imgsz[0], s=stride)  # check image size

    # Dataloader
    if webcam:
        show_vid = check_imshow()
        cudnn.benchmark = True  # set True to speed up constant image size inference
        dataset = LoadStreams(source, img_size=imgsz, stride=stride)
        nr_sources = 1
    else:
        dataset = LoadImages(source, img_size=imgsz, stride=stride)
        nr_sources = 1
    vid_path, vid_writer, txt_path = [None] * nr_sources, [None] * nr_sources, [None] * nr_sources

    # initialize StrongSORT
    cfg = get_config()
    cfg.merge_from_file(config_strongsort)

    # Create as many strong sort instances as there are video sources
    strongsort_list = []
    for i in range(nr_sources):
        strongsort_list.append(
            StrongSORT(
                strong_sort_weights,
                device,
                half,
                max_dist=cfg.STRONGSORT.MAX_DIST,
                max_iou_distance=cfg.STRONGSORT.MAX_IOU_DISTANCE,
                max_age=cfg.STRONGSORT.MAX_AGE,
                n_init=cfg.STRONGSORT.N_INIT,
                nn_budget=cfg.STRONGSORT.NN_BUDGET,
                mc_lambda=cfg.STRONGSORT.MC_LAMBDA,
                ema_alpha=cfg.STRONGSORT.EMA_ALPHA,

            )
        )
        strongsort_list[i].model.warmup()
    outputs = [None] * nr_sources
    
    colors = [[random.randint(0, 255) for _ in range(3)] for _ in names]

    # Run tracking
    dt, seen = [0.0, 0.0, 0.0, 0.0], 0
    curr_frames, prev_frames = [None] * nr_sources, [None] * nr_sources
    for frame_idx, (path, im, im0s, vid_cap) in enumerate(dataset):
        s = ''
        t1 = time_synchronized()
        im = torch.from_numpy(im).to(device)
        im = im.half() if half else im.float()  # uint8 to fp16/32
        im /= 255.0  # 0 - 255 to 0.0 - 1.0
        if len(im.shape) == 3:
            im = im[None]  # expand for batch dim
        t2 = time_synchronized()
        dt[0] += t2 - t1

        # Inference
        visualize = increment_path(save_dir / Path(path[0]).stem, mkdir=True) if visualize else False
        pred, im2 = model(im)
        t3 = time_synchronized()
        dt[1] += t3 - t2

        # Apply NMS
        pred = non_max_suppression_kpt(pred,
                                       conf_thres,  # Confidence Threshold
                                       iou_thres,  # IoU Threshold
                                       nc=model.yaml['nc'],  # Number of Classes
                                       nkpt=model.yaml['nkpt'],  # Number of Keypoints
                                       kpt_label=True)
        
        with torch.no_grad():
          pred_kpt = output_to_keypoint(pred)
        
        dt[2] += time_synchronized() - t3
        
        # Process detections
        for i, pose in enumerate(pred):  # detections per image
            seen += 1
            if webcam:  # nr_sources >= 1
                p, im0, _ = path[i], im0s[i].copy(), dataset.count
                p = Path(p)  # to Path
                s += f'{i}: '
                txt_file_name = p.name
                save_path = str(save_dir / p.name)  # im.jpg, vid.mp4, ...
            else:
                p, im0, _ = path, im0s.copy(), getattr(dataset, 'frame', 0)
                p = Path(p)  # to Path
                # video file
                if source.endswith(VID_FORMATS):
                    txt_file_name = p.stem
                    save_path = str(save_dir / p.name)  # im.jpg, vid.mp4, ...
                # folder with imgs
                else:
                    txt_file_name = p.parent.name  # get folder name containing current img
                    save_path = str(save_dir / p.parent.name)  # im.jpg, vid.mp4, ...

            curr_frames[i] = im0

            txt_path = str(str(save_dir) + '/tracks' + txt_file_name)  # im.txt
            s += '%gx%g ' % im.shape[2:]  # print string
            imc = im0.copy() if save_crop else im0  # for save_crop

            if cfg.STRONGSORT.ECC:  # camera motion compensation
                strongsort_list[i].tracker.camera_update(prev_frames[i], curr_frames[i])
            
            det = pred[0]
            # det_list.append(det)
            #return det    # 디버그 용
            if det is not None and len(det):
                # Rescale boxes from img_size to im0 size
                det[:, :4] = scale_coords(im.shape[2:], det[:, :4], im0.shape).round()

                # Print results
                for c in set(det[:, -1]):
                    n = (det[:, -1] == c).sum()  # detections per class
                    s += f"{n} {names[int(c)]}{'s' * (n > 1)}, "  # add to string

                xywhs = xyxy2xywh(det[:, 0:4])
                confs = det[:, 4]
                clss = det[:, 5]

                # pass detections to strongsort
                t4 = time_synchronized()
                outputs[i] = strongsort_list[i].update(xywhs.cpu(), confs.cpu(), clss.cpu(), im0)
                t5 = time_synchronized()
                dt[3] += t5 - t4

                # draw boxes for visualization
                if len(outputs[i]) > 0:
                    for j, (output, conf) in enumerate(zip(outputs[i], confs)):
    
                        bboxes = output[0:4]
                        id = output[4]
                        cls = output[5]

                        if save_txt:
                            # to MOT format
                            bbox_left = output[0]
                            bbox_top = output[1]
                            bbox_w = output[2] - output[0]
                            bbox_h = output[3] - output[1]
                            # Write MOT compliant results to file
                            with open(txt_path + '.txt', 'a') as f:
                                f.write(('%g ' * 10 + '\n') % (frame_idx + 1, id, bbox_left,  # MOT format
                                                               bbox_top, bbox_w, bbox_h, -1, -1, -1, i))

                        if save_vid or save_crop or show_vid:  # Add bbox to image
                            #c = int(cls)  # integer class
                            c = 0
                            id = int(id)  # integer id
                            label = None if hide_labels else (f'{id} {names[c]}' if hide_conf else \
                                (f'{id} {conf:.2f}' if hide_class else f'{id} {names[c]} {conf:.2f}'))
                            plot_one_box(bboxes, im0, label=label, color=colors[c], line_thickness=2)
                            if save_crop:
                                txt_file_name = txt_file_name if (isinstance(path, list) and len(path) > 1) else ''
                                save_one_box(bboxes, imc, file=save_dir + '/crops' / txt_file_name / names[c] / f'{id}' / f'{p.stem}.jpg', BGR=True)
                    det[j, 5] = output[4]
                print(f'{s}Done. YOLO:({t3 - t2:.3f}s), StrongSORT:({t5 - t4:.3f}s)')

            else:
                strongsort_list[i].increment_ages()
                print('No detections')

            det_list.append(det)

            # Stream results
            if show_vid:
                cv2.imshow(str(p), im0)
                cv2.waitKey(1)  # 1 millisecond

            # Save results (image with detections)
            if save_vid:
                if vid_path[i] != save_path:  # new video
                    vid_path[i] = save_path
                    if isinstance(vid_writer[i], cv2.VideoWriter):
                        vid_writer[i].release()  # release previous video writer
                    if vid_cap:  # video
                        fps = vid_cap.get(cv2.CAP_PROP_FPS)
                        w = int(vid_cap.get(cv2.CAP_PROP_FRAME_WIDTH))
                        h = int(vid_cap.get(cv2.CAP_PROP_FRAME_HEIGHT))
                    else:  # stream
                        fps, w, h = 30, im0.shape[1], im0.shape[0]
                    save_path = str(Path(save_path).with_suffix('.mp4'))  # force *.mp4 suffix on results videos
                    vid_writer[i] = cv2.VideoWriter(save_path, cv2.VideoWriter_fourcc(*'mp4v'), fps, (w, h))
                vid_writer[i].write(im0)

            prev_frames[i] = curr_frames[i]

    # Print results
    t = tuple(x / seen * 1E3 for x in dt)  # speeds per image
    print(f'Speed: %.1fms pre-process, %.1fms inference, %.1fms NMS, %.1fms strong sort update per image at shape {(1, 3, imgsz, imgsz)}' % t)
    if save_txt or save_vid:
        s = f"\n{len(list(save_dir.glob('track/*.txt')))} tracks saved to {save_dir / 'track'}" if save_txt else ''
        print(f"Results saved to {colorstr('bold', save_dir)}{s}")
    if update:
        strip_optimizer(yolo_weights)  # update model (to fix SourceChangeWarning)
    
    return(det_list)

In [7]:
def loading_yolov7_model(yolomodel, device):
    """
    Loading yolov7 model
    """
    print("Loading model:", yolomodel)
    model = torch.load(yolomodel, map_location=device)['model']
    model.float().eval()

    if torch.cuda.is_available():
        # half() turns predictions into float16 tensors
        # which significantly lowers inference time
        model.to(device)

    return model

In [209]:
det_list = run()

cpu
Loading model: /content/drive/Othercomputers/내 노트북/Forked_Models/Yolov7_StrongSORT_OSNet/yolov7/yolov7-w6-pose.pt


Downloading...
From: https://drive.google.com/uc?id=1Kkx2zW89jq_NETu4u42CFZTMVD5Hwm6e
To: /content/drive/Othercomputers/내 노트북/Forked_Models/승객 승하차 분류 유효성/AIhub에서 배포한 도커이미지 파일 원본/docker_files/fs_get_on_off/osnet_x0_25_msmt17.pt
100%|██████████| 9.34M/9.34M [00:00<00:00, 20.5MB/s]


Model: osnet_x0_25
- params: 203,568
- flops: 82,316,000
Successfully loaded pretrained weights from "osnet_x0_25_msmt17.pt"
** The following layers are discarded due to unmatched keys or layer size: ['classifier.weight', 'classifier.bias']
No detections
No detections
No detections
No detections
No detections
No detections
No detections
No detections
No detections
No detections
No detections
No detections
No detections
No detections
No detections
No detections
No detections
No detections
No detections
No detections
No detections
No detections
No detections
No detections
No detections
No detections
640x1088 1 person, Done. YOLO:(3.334s), StrongSORT:(0.058s)
No detections
No detections
No detections
No detections
No detections
No detections
640x1088 1 person, Done. YOLO:(3.341s), StrongSORT:(0.036s)
No detections
No detections
No detections
No detections
No detections
No detections
No detections
No detections
No detections
No detections
No detections
640x1088 1 person, 1 person, 1 person

In [210]:
det_list_2 = det_list #det_list 백업

## Make Json File

In [211]:
import json
import cv2
from tqdm import notebook, tqdm

from PIL import Image
from IPython.display import Image

In [212]:
# 파일 이름 리스트로 저장하는 함수
def extract_file_name(url):
  file_list = os.listdir(url)
  file_name = []
  for file in file_list:
    file_name.append(file.split('.')[0])
  return sorted(file_name)

In [213]:
a1 = extract_file_name("/content/drive/Othercomputers/내 노트북/Forked_Models/Data_A/Image_A/")
a2 = extract_file_name("/content/drive/Othercomputers/내 노트북/Forked_Models/Data_A/Label_A/")
print(len(a1))
print(len(a2))
print(a1)

116
116
['[district]attend_003A_000', '[district]attend_003A_003', '[district]attend_003A_006', '[district]attend_003A_009', '[district]attend_003A_012', '[district]attend_003A_015', '[district]attend_003A_018', '[district]attend_003A_021', '[district]attend_003A_024', '[district]attend_003A_027', '[district]attend_003A_030', '[district]attend_003A_033', '[district]attend_003A_036', '[district]attend_003A_039', '[district]attend_003A_042', '[district]attend_003A_045', '[district]attend_003A_048', '[district]attend_003A_051', '[district]attend_003A_054', '[district]attend_003A_057', '[district]attend_003A_060', '[district]attend_003A_063', '[district]attend_003A_066', '[district]attend_003A_069', '[district]attend_003A_072', '[district]attend_003A_075', '[district]attend_003A_078', '[district]attend_003A_081', '[district]attend_003A_084', '[district]attend_003A_087', '[district]attend_003A_090', '[district]attend_003A_093', '[district]attend_003A_096', '[district]attend_003A_099', '[dis

In [ ]:
# for i in range(len(det_list)):
#   for j in range(len(det_list[i])):
#     # bbox
#     if len(det_list[i][j][:4].tolist()) == 0:
#       print("None")
#     else:
#       print(det_list[i][j][:4].tolist())

In [ ]:
# files = tqdm(extract_file_name("/content/drive/Othercomputers/내 노트북/Forked_Models/Data_A/Image_A/"))
# i=0

# for file in files:
#   files.set_description(f"Processing {file}")
#   imgfile = "/content/drive/Othercomputers/내 노트북/Forked_Models/Data_A/Image_A/{}.jpg".format(file)
#   img = cv2.imread(imgfile)
#   with open("/content/drive/Othercomputers/내 노트북/Forked_Models/Data_A/Label_A/{}.json".format(file), 'r') as f:
#     json_data = json.load(f)
  
#   h, w, c = img.shape
#   json_data["info"]["height"] = str(h)
#   json_data["info"]["width"] = str(w)

#   # img path
#   json_data["info"]["img_path"] = str(imgfile)

#   # 탐지 사람 수 만큼 반복 
#   for j in range(len(det_list[i])):
#     if len(json_data["annotations"]) != None:
#       # bbox
#       json_data["annotations"][j]["bbox"] = det_list[i][j][:4].tolist()
#       # keypoints 길이
#       json_data["annotations"][j]["num_keypoints"] = len(det_list[i][j][6:].tolist())/3
#       # keypoints 좌표 
#       json_data["annotations"][j]["keypoints"] = det_list[i][j][6:].tolist()
  
#   with open("/content/drive/Othercomputers/내 노트북/Forked_Models/Data_A/Image_A/{}.json".format(file), 'w') as f:
#     json.dump(json_data, f, indent = 4)
#   i+=1


In [214]:
files = tqdm(extract_file_name("/content/drive/Othercomputers/내 노트북/Forked_Models/Data_A/Image_A/"))
i=0
for file in files:
  files.set_description(f"Processing {file}")
  imgfile = "/content/drive/Othercomputers/내 노트북/Forked_Models/Data_A/Image_A/{}.jpg".format(file)
  img = cv2.imread(imgfile)
  with open("/content/drive/Othercomputers/내 노트북/Forked_Models/Data_A/Label_A/{}.json".format(file), 'r') as f:
    json_data = json.load(f)
  
  h, w, c = img.shape
  json_data["info"]["height"] = float(h)
  json_data["info"]["width"] = float(w)

  # img path
  json_data["info"]["img_path"] = str(imgfile)

  json_data["annotations"] = []

  if len(det_list[i]) > 0:
    for j in range(len(det_list[i].tolist())):
      print(int(det_list[i][j][5]))
      dic = {"id" : int(det_list[i][j][5]),
             "bbox" : det_list[i][j][:4].tolist(),
             "occluded" : None,
             "num_keypoints" : len(det_list[i][j][6:].tolist())/3,
             "keypoints" : det_list[i][j][6:].tolist(),
             "action": "None",
             "age": "None",
             "disabled": None,
             "mask": None,
             "get_on": None,
             "get_off": None}
      json_data["annotations"].append(dic)
      
  
    with open("/content/drive/Othercomputers/내 노트북/Forked_Models/Data_A/Label_A/{}.json".format(file), 'w') as f:
      json.dump(json_data, f, indent = 4)
    
  else:
    json_data["annotations"] = []
    with open("/content/drive/Othercomputers/내 노트북/Forked_Models/Data_A/Label_A/{}.json".format(file), 'w') as f:
      json.dump(json_data, f, indent = 4)
  
  i+=1


Processing [district]attend_003A_093:  25%|██▌       | 29/116 [00:01<00:03, 22.13it/s]

0


Processing [district]attend_003A_111:  33%|███▎      | 38/116 [00:01<00:03, 21.29it/s]

0


Processing [district]attend_003A_147:  43%|████▎     | 50/116 [00:02<00:03, 20.42it/s]

...

0
0


Processing [district]attend_003A_333:  95%|█████████▍| 110/116 [00:06<00:00, 15.54it/s]

0


Processing [district]attend_003A_345: 100%|██████████| 116/116 [00:06<00:00, 17.53it/s]

0


##Show Results

In [ ]:
# !ffmpeg -i "/content/drive/Othercomputers/내 노트북/Forked_Models/Yolov7_StrongSORT_OSNet/runs/track/exp/sample.mp4" sample_video.mp4

ffmpeg version 4.2.7-0ubuntu0.1 Copyright (c) 2000-2022 the FFmpeg developers
  built with gcc 9 (Ubuntu 9.4.0-1ubuntu1~20.04.1)
  configuration: --prefix=/usr --extra-version=0ubuntu0.1 --toolchain=hardened --libdir=/usr/lib/x86_64-linux-gnu --incdir=/usr/include/x86_64-linux-gnu --arch=amd64 --enable-gpl --disable-stripping --enable-avresample --disable-filter=resample --enable-avisynth --enable-gnutls --enable-ladspa --enable-libaom --enable-libass --enable-libbluray --enable-libbs2b --enable-libcaca --enable-libcdio --enable-libcodec2 --enable-libflite --enable-libfontconfig --enable-libfreetype --enable-libfribidi --enable-libgme --enable-libgsm --enable-libjack --enable-libmp3lame --enable-libmysofa --enable-libopenjpeg --enable-libopenmpt --enable-libopus --enable-libpulse --enable-librsvg --enable-librubberband --enable-libshine --enable-libsnappy --enable-libsoxr --enable-libspeex --enable-libssh --enable-libtheora --enable-libtwolame --enable-libvidstab --enable-libvorbis --e

In [ ]:
# from IPython.display import HTML
# from base64 import b64encode
# mp4 = open('sample_video.mp4','rb').read()
# data_url = "data:video/mp4;base64," + b64encode(mp4).decode()

In [ ]:
# HTML("""
# <video controls width="1000">
#       <source src="%s" type="video/mp4">
# </video>
# """ % data_url)

#2. Action Recognition

In [215]:
%cd "/content/drive/Othercomputers/내 노트북/Forked_Models/승객 승하차 분류 유효성/AIhub에서 배포한 도커이미지 파일 원본/docker_files/fs_get_on_off"

/content/drive/Othercomputers/내 노트북/Forked_Models/승객 승하차 분류 유효성/AIhub에서 배포한 도커이미지 파일 원본/docker_files/fs_get_on_off


In [216]:
 #from utils.data import GetOnOffData

#__getOriginalDataList 메소드 입력 부분 약간 튜닝 
from __future__ import print_function
from __future__ import absolute_import
from __future__ import division

from glob import glob
import os
from tqdm import tqdm
from functools import cmp_to_key
import json
import random
import math
import numpy as np
from datetime import datetime
from pytz import timezone
import shutil
from tensorflow import keras
import logging
import traceback
import tensorflow as tf
logging.basicConfig(level=logging.ERROR)

## Make Input

In [217]:
class GetOnOffData2:
    def __init__(self, original_data_dir, get_on_off_data_dir, dataset_dir, train_val_rate):
        self.original_data_list = self.__getOriginalDataList(original_data_dir)
        self.original_data_dir = original_data_dir
        self.get_on_off_data_dir = get_on_off_data_dir
        self.train_val_rate = train_val_rate
        self.original_num = 0
        self.get_on_json_list = []
        self.get_off_json_list = []
        self.idle_json_list = []
        self.get_on_num = 0
        self.get_off_num = 0
        self.idle_num = 0
        self.dataset_dir = dataset_dir
        self.train_get_on_num = 0
        self.val_get_on_num = 0
        self.test_get_on_num = 0
        self.train_get_off_num = 0
        self.val_get_off_num = 0
        self.test_get_off_num = 0
        self.train_idle_num = 0
        self.val_idle_num = 0
        self.test_idle_num = 0
        self.train_num = 0
        self.val_num = 0
        self.test_num = 0
        self.train_list = []
        self.val_list = []
        self.test_list = []


    def compare_json(self, x, y):
        x_index = [pos for pos, char in enumerate(x) if char == '_']
        x_index = x_index[-1]
        x_index += 1
        y_index = [pos for pos, char in enumerate(y) if char == '_']
        y_index = y_index[-1]
        y_index += 1
        x_int = int(x[x_index:-5])
        y_int = int(y[y_index:-5])
        if (x_int < y_int):
            return -1
        elif (x_int >= y_int):
            return 1

    def __getOriginalDataList(self, original_data_dir):
        # Get Folder List
        folder_list = glob(original_data_dir)
        folder_list = [file for file in folder_list if os.path.isdir(file)]
        folder_list = sorted(folder_list)
        random.seed(0)
        random.shuffle(folder_list)
        print(len(folder_list))
        # list parameters
        dst = []

        for folder in tqdm(folder_list):
            # Json file list
            json_list = os.listdir(folder)
            json_list = [file for file in json_list if file.endswith('.json')]
            json_list = sorted(json_list, key=cmp_to_key(self.compare_json))

            # Get json path
            tmp_list = []
            for json_file_name in json_list:
                tmp_list.append(os.path.join(folder, json_file_name))

            dst.append(tmp_list)

        return dst

    def getOriginalDataLog(self):
        dst = ''
        json_count = 0
        for folder in self.original_data_list:
            for json_path in folder:
                json_count += 1
                dst += str(json_count) + '. ' + json_path + '\n'
                print(str(json_count) + '. ' + json_path)
        self.original_num = json_count

        return dst

    def makeGetOnOffData(self):
        # Get Model(AIhub에서 제공한 모델 원본)
        tent_model = keras.models.load_model("/content/drive/Othercomputers/내 노트북/Forked_Models/승객 승하차 분류 유효성/AIhub에서 배포한 도커이미지 파일 원본/docker_files/fs_get_on_off/saved_models/fs_lstm_get_on_off-029.h5")

        # Make dir
        get_on_dir = os.path.join(self.get_on_off_data_dir, 'get_on')
        get_off_dir = os.path.join(self.get_on_off_data_dir, 'get_off')
        idle_dir = os.path.join(self.get_on_off_data_dir, 'idle')
        os.makedirs(get_on_dir, exist_ok=True)
        os.makedirs(get_off_dir, exist_ok=True)
        os.makedirs(idle_dir, exist_ok=True)

        # Count Parameters
        get_on_count = 0
        get_off_count = 0
        idle_count = 0

        # file name parameters
        get_on_data_name = 'get_on_'
        get_off_data_name = 'get_off_'
        idle_data_name = 'idle_'
        print(self.original_data_list)
        # Make get on off data
        for json_list in tqdm(self.original_data_list):
            # Get Passenger Data
            for i in range(len(json_list) - 2):
                # Get Json data
                json_path_1 = os.path.join(json_list[i])
                json_path_2 = os.path.join(json_list[i + 1])
                json_path_3 = os.path.join(json_list[i + 2])
                try:
                    with open(json_path_1, 'r') as json_file:
                        json_data_1 = json.load(json_file)
                except Exception:
                    raise Exception('json_path_1: ', json_path_1)
                try:
                    with open(json_path_2, 'r') as json_file:
                        json_data_2 = json.load(json_file)
                except Exception:
                    raise Exception('json_path_2: ', json_path_2)
                try:
                    with open(json_path_3, 'r') as json_file:
                        json_data_3 = json.load(json_file)
                except Exception:
                    raise Exception('json_path_3: ', json_path_3)

                # Get Img width & height
                width = json_data_1['info']['width']
                height = json_data_1['info']['height']

                # Get Valid data id and Append data
                if len(json_data_1['annotations']) != 0 and len(json_data_2['annotations']) != 0 and len(
                        json_data_3['annotations']) != 0:
                    for annotation_1 in json_data_1['annotations']:
                        id_1 = annotation_1['id']
                        for annotation_2 in json_data_2['annotations']:
                            id_2 = annotation_2['id']
                            if id_1 != id_2:
                                continue
                            else:
                                for r, annotation_3 in enumerate(json_data_3['annotations']):
                                    id_3 = annotation_3['id']
                                    if id_2 != id_3:
                                        continue
                                    else:
                                        # Checking neck keypoint is exist
                                        if annotation_1['keypoints'][26] == 0 and annotation_2['keypoints'][26] == 0 and \
                                                annotation_3['keypoints'][26] == 0:
                                            print(annotation_1['keypoints'][26])
                                            break
                                        # Checking head keypoint is exist
                                        elif annotation_1['keypoints'][29] == 0 and annotation_2['keypoints'][
                                            29] == 0 and annotation_3['keypoints'][29] == 0:
                                            print(annotation_1['keypoints'][29])
                                            break
                                        # Checking right shoulder keypoint is exist
                                        elif annotation_1['keypoints'][38] == 0 and annotation_2['keypoints'][
                                            38] == 0 and annotation_3['keypoints'][38] == 0:
                                            print(annotation_1['keypoints'][38])
                                            break
                                        # Checking left shoulder keypoint is exist
                                        elif annotation_1['keypoints'][41] == 0 and annotation_2['keypoints'][
                                            41] == 0 and annotation_3['keypoints'][41] == 0:
                                            print(annotation_1['keypoints'][41])
                                            break

                                        # Get Data of neck keypoint
                                        neck_x_1 = annotation_1['keypoints'][24] / width
                                        neck_y_1 = annotation_1['keypoints'][25] / height
                                        neck_x_2 = annotation_2['keypoints'][24] / width
                                        neck_y_2 = annotation_2['keypoints'][25] / height
                                        neck_x_3 = annotation_3['keypoints'][24] / width
                                        neck_y_3 = annotation_3['keypoints'][25] / height

                                        # Get Data of head keypoint
                                        head_x_1 = annotation_1['keypoints'][27] / width
                                        head_y_1 = annotation_1['keypoints'][28] / height
                                        head_x_2 = annotation_2['keypoints'][27] / width
                                        head_y_2 = annotation_2['keypoints'][28] / height
                                        head_x_3 = annotation_3['keypoints'][27] / width
                                        head_y_3 = annotation_3['keypoints'][28] / height

                                        # Get Data of right shoulder keypoint
                                        r_shoulder_x_1 = annotation_1['keypoints'][36] / width
                                        r_shoulder_y_1 = annotation_1['keypoints'][37] / height
                                        r_shoulder_x_2 = annotation_2['keypoints'][36] / width
                                        r_shoulder_y_2 = annotation_2['keypoints'][37] / height
                                        r_shoulder_x_3 = annotation_3['keypoints'][36] / width
                                        r_shoulder_y_3 = annotation_3['keypoints'][37] / height

                                        # Get Data of left shoulder keypoint
                                        l_shoulder_x_1 = annotation_1['keypoints'][39] / width
                                        l_shoulder_y_1 = annotation_1['keypoints'][40] / height
                                        l_shoulder_x_2 = annotation_2['keypoints'][39] / width
                                        l_shoulder_y_2 = annotation_2['keypoints'][40] / height
                                        l_shoulder_x_3 = annotation_3['keypoints'][39] / width
                                        l_shoulder_y_3 = annotation_3['keypoints'][40] / height

                                        # Get Vector of neck->rShoulder
                                        vector_r_shoulder_x_1 = r_shoulder_x_1 - neck_x_1
                                        vector_r_shoulder_y_1 = r_shoulder_y_1 - neck_y_1
                                        vector_r_shoulder_x_2 = r_shoulder_x_2 - neck_x_2
                                        vector_r_shoulder_y_2 = r_shoulder_y_2 - neck_y_2
                                        vector_r_shoulder_x_3 = r_shoulder_x_3 - neck_x_3
                                        vector_r_shoulder_y_3 = r_shoulder_y_3 - neck_y_3

                                        # Get Vector of neck->lShoulder
                                        vector_l_shoulder_x_1 = l_shoulder_x_1 - neck_x_1
                                        vector_l_shoulder_y_1 = l_shoulder_y_1 - neck_y_1
                                        vector_l_shoulder_x_2 = l_shoulder_x_2 - neck_x_2
                                        vector_l_shoulder_y_2 = l_shoulder_y_2 - neck_y_2
                                        vector_l_shoulder_x_3 = l_shoulder_x_3 - neck_x_3
                                        vector_l_shoulder_y_3 = l_shoulder_y_3 - neck_y_3

                                        # Get Vector of neck->head
                                        vector_head_x_1 = head_x_1 - neck_x_1
                                        vector_head_y_1 = head_y_1 - neck_y_1
                                        vector_head_x_2 = head_x_2 - neck_x_2
                                        vector_head_y_2 = head_y_2 - neck_y_2
                                        vector_head_x_3 = head_x_3 - neck_x_3
                                        vector_head_y_3 = head_y_3 - neck_y_3

                                        # Push Data
                                        data = [[0 for col in range(8)] for row in range(3)]
                                        data[0] = [neck_x_1, neck_y_1,
                                                   vector_head_x_1, vector_head_y_1,
                                                   vector_r_shoulder_x_1, vector_r_shoulder_y_1,
                                                   vector_l_shoulder_x_1, vector_l_shoulder_y_1]
                                        data[1] = [neck_x_2, neck_y_2,
                                                   vector_head_x_2, vector_head_y_2,
                                                   vector_r_shoulder_x_2, vector_r_shoulder_y_2,
                                                   vector_l_shoulder_x_2, vector_l_shoulder_y_2]
                                        data[2] = [neck_x_3, neck_y_3,
                                                   vector_head_x_3, vector_head_y_3,
                                                   vector_r_shoulder_x_3, vector_r_shoulder_y_3,
                                                   vector_l_shoulder_x_3, vector_l_shoulder_y_3]

                                        data_dict = dict()
                                        data_dict['data'] = data
                                        data_dict['original_data'] = []
                                        for i in range(3):
                                            tmp_dict = dict()
                                            tmp_dict['time_step'] = i + 1
                                            if i == 0:
                                                tmp_dict['original_data_path'] = json_path_1
                                            elif i == 1:
                                                tmp_dict['original_data_path'] = json_path_2
                                            else:
                                                tmp_dict['original_data_path'] = json_path_3
                                            tmp_dict['id'] = annotation_3['id']

                                            data_dict['original_data'].append(tmp_dict)


                                        # Count num of get_on get_off idle
                                        if annotation_3['get_on']:
                                            get_on_count += 1
                                            data_dict['label'] = 0
                                            json_file_name = get_on_data_name + str(get_on_count) + '.json'
                                            json_file_path = os.path.join(get_on_dir, json_file_name)
                                            if not os.path.exists(json_file_path):
                                                with open(json_file_path, 'w') as f:
                                                    json.dump(data_dict, f, indent=4)

                                        elif annotation_3['get_off']:
                                            get_off_count += 1
                                            data_dict['label'] = 1
                                            json_file_name = get_off_data_name + str(get_off_count) + '.json'
                                            json_file_path = os.path.join(get_off_dir, json_file_name)
                                            if not os.path.exists(json_file_path):
                                                with open(json_file_path, 'w') as f:
                                                    json.dump(data_dict, f, indent=4)

                                        else:
                                            idle_count += 1
                                            data_dict['label'] = 2
                                            json_file_name = idle_data_name + str(idle_count) + '.json'
                                            json_file_path = os.path.join(idle_dir, json_file_name)
                                            if not os.path.exists(json_file_path):
                                                with open(json_file_path, 'w') as f:
                                                    json.dump(data_dict, f, indent=4)

                                        

                                        ############################################
                                        ########의도분석 모델 결과 얻는 부분########
                                        ############################################
                                        with open(json_file_path, 'r') as f:  # 1)생성한 input json 파일에서 모델 입력값 얻어오기
                                            json_data = json.load(f)
                                        
                                        input_data = [json_data['data']]
                                        print(tf.convert_to_tensor(input_data))
                                        prediction = tent_model(tf.convert_to_tensor(input_data))
                                        prediction = np.argmax(prediction, axis = 1)
                                        print(prediction)

                                        if prediction[0] == 0:
                                          with open(json_path_3, 'r') as file:
                                              temp_json = json.load(file)
                                          temp_json["annotations"][r]["get_on"] = True
                                          temp_json["annotations"][r]["get_off"] = False
                                          print(json_path_3)
                                          with open(json_path_3, 'w') as file:
                                              json.dump(temp_json, file, indent=4)

                                        elif prediction[0] == 1:
                                          with open(json_path_3, 'r') as file:
                                              temp_json = json.load(file)
                                          temp_json["annotations"][r]["get_off"] = True
                                          temp_json["annotations"][r]["get_on"] = False
                                          print(json_path_3)
                                          with open(json_path_3, 'w') as file:
                                              json.dump(temp_json, file, indent=4)
                                        
                                        else:
                                          with open(json_path_3, 'r') as file:
                                              temp_json = json.load(file)
                                          temp_json["annotations"][r]["get_on"] = False
                                          temp_json["annotations"][r]["get_off"] = False
                                          print(json_path_3)
                                          with open(json_path_3, 'w') as file:
                                              json.dump(temp_json, file, indent=4)
                                        
                                        ############################################

                                        break
                            break

        self.get_on_num = get_on_count
        self.get_off_num = get_off_count
        self.idle_num = idle_count

    def getGetOnDataLog(self):
        dst = ''

        # Get dir
        get_on_dir = os.path.join(self.get_on_off_data_dir, 'get_on')

        # Get json list
        json_list = glob(get_on_dir + '/*')
        json_list = sorted(json_list, key=cmp_to_key(self.compare_json))
        self.get_on_json_list = json_list

        for i in range(self.get_on_num):
            tmp_str = str(i + 1) + '. ' + json_list[i] + '\n'
            with open(json_list[i], 'r') as f:
                json_data = json.load(f)
            for original_data_dict in json_data['original_data']:
                time_step = original_data_dict['time_step']
                original_data_path = original_data_dict['original_data_path']
                id = original_data_dict['id']
                tmp_str += '\ttime_step: {0:d}, original_data_path: {1:s}, id: {2:d}\n'.format(time_step, original_data_path, id)
            dst += tmp_str
            print(tmp_str)

        return dst

    def getGetOffDataLog(self):
        dst = ''

        # Get dir
        get_off_dir = os.path.join(self.get_on_off_data_dir, 'get_off')

        # Get json list
        json_list = glob(get_off_dir + '/*')
        json_list = sorted(json_list, key=cmp_to_key(self.compare_json))
        self.get_off_json_list = json_list

        for i in range(self.get_off_num):
            tmp_str = str(i + 1) + '. ' + json_list[i] + '\n'
            with open(json_list[i], 'r') as f:
                json_data = json.load(f)
            for original_data_dict in json_data['original_data']:
                time_step = original_data_dict['time_step']
                original_data_path = original_data_dict['original_data_path']
                id = original_data_dict['id']
                tmp_str += '\ttime_step: {0:d}, original_data_path: {1:s}, id: {2:d}\n'.format(time_step, original_data_path, id)
            dst += tmp_str
            print(tmp_str)

        return dst

    def getIdleDataLog(self):
        dst = ''

        # Get dir
        idle_dir = os.path.join(self.get_on_off_data_dir, 'idle')

        # Get json list
        json_list = glob(idle_dir + '/*')
        json_list = sorted(json_list, key=cmp_to_key(self.compare_json))
        self.idle_json_list = json_list

        for i in range(self.idle_num):
            tmp_str = str(i + 1) + '. ' + json_list[i] + '\n'
            with open(json_list[i], 'r') as f:
                json_data = json.load(f)
            for original_data_dict in json_data['original_data']:
                time_step = original_data_dict['time_step']
                original_data_path = original_data_dict['original_data_path']
                id = original_data_dict['id']
                tmp_str += '\ttime_step: {0:d}, original_data_path: {1:s}, id: {2:d}\n'.format(time_step, original_data_path, id)
            dst += tmp_str
            print(tmp_str)

        return dst

    def divideDataByRate(self):
        # Get train/val/test dir and make dir
        train_dir = os.path.join(self.dataset_dir, 'training')
        val_dir = os.path.join(self.dataset_dir, 'validation')
        test_dir = os.path.join(self.dataset_dir, 'test')
        os.makedirs(train_dir, exist_ok=True)
        os.makedirs(val_dir, exist_ok=True)
        os.makedirs(test_dir, exist_ok=True)

        # Divide data by rate
        self.train_get_on_num = math.ceil(self.get_on_num * self.train_val_rate[0])  # 올림
        self.val_get_on_num = math.floor(self.get_on_num * self.train_val_rate[1])  # 내림
        self.test_get_on_num = self.get_on_num - self.train_get_on_num - self.val_get_on_num

        self.train_get_off_num = math.ceil(self.get_off_num * self.train_val_rate[0])  # 올림
        self.val_get_off_num = math.floor(self.get_off_num * self.train_val_rate[1])  # 내림
        self.test_get_off_num = self.get_off_num - self.train_get_off_num - self.val_get_off_num

        self.train_idle_num = math.ceil(self.idle_num * self.train_val_rate[0])  # 올림
        self.val_idle_num = math.floor(self.idle_num * self.train_val_rate[1])  # 내림
        self.test_idle_num = self.idle_num - self.train_idle_num - self.val_idle_num

        self.train_num = self.train_get_on_num + self.train_get_off_num + self.train_idle_num
        self.val_num = self.val_get_on_num + self.val_get_off_num + self.val_idle_num
        self.test_num = self.test_get_on_num + self.test_get_off_num + self.test_idle_num

        # Get train/val/test list
        train_json_list = self.get_on_json_list[:self.train_get_on_num] + \
                          self.get_off_json_list[:self.train_get_off_num] + \
                          self.idle_json_list[:self.train_idle_num]

        val_json_list = self.get_on_json_list[self.train_get_on_num:self.train_get_on_num + self.val_get_on_num] + \
                        self.get_off_json_list[self.train_get_off_num:self.train_get_off_num + self.val_get_off_num] + \
                        self.idle_json_list[self.train_idle_num:self.train_idle_num + self.val_idle_num]

        test_json_list = self.get_on_json_list[self.train_get_on_num + self.val_get_on_num:] + \
                         self.get_off_json_list[self.train_get_off_num + self.val_get_off_num:] + \
                         self.idle_json_list[self.train_idle_num + self.val_idle_num:]

        # Copy get_on/get_off/idle json files to train/validation/test dataset dir
        for json_path in tqdm(train_json_list):
            new_json_path = os.path.join(train_dir, os.path.basename(json_path))
            self.train_list.append(new_json_path)
            if not os.path.exists(new_json_path):
                shutil.copyfile(json_path, new_json_path)
        for json_path in tqdm(val_json_list):
            new_json_path = os.path.join(val_dir, os.path.basename(json_path))
            self.val_list.append(new_json_path)
            if not os.path.exists(new_json_path):
                shutil.copyfile(json_path, new_json_path)
        for json_path in tqdm(test_json_list):
            new_json_path = os.path.join(test_dir, os.path.basename(json_path))
            self.test_list.append(new_json_path)
            if not os.path.exists(new_json_path):
                shutil.copyfile(json_path, new_json_path)

    def getTrainDataLog(self):
        dst = ''
        for idx in range(self.train_num):
            json_path = self.train_list[idx]
            dst += '{0:d}. {1:s}'.format(idx + 1, json_path) + '\n'
            print('{0:d}. {1:s}'.format(idx + 1, json_path))
        return dst

    def getValDataLog(self):
        dst = ''
        for idx in range(self.val_num):
            json_path = self.val_list[idx]
            dst += '{0:d}. {1:s}'.format(idx + 1, json_path) + '\n'
            print('{0:d}. {1:s}'.format(idx + 1, json_path))
        return dst

    def getTestDataLog(self):
        dst = ''
        for idx in range(self.test_num):
            json_path = self.test_list[idx]
            dst += '{0:d}. {1:s}'.format(idx + 1, json_path) + '\n'
            print('{0:d}. {1:s}'.format(idx + 1, json_path))
        return dst

    def generateGetOnOffData(self):
        # Parameters
        fmt = '%Y-%m-%d %H:%M:%S %Z%z'
        log_str = ''

        # Get Original Data Log str
        cur_time = datetime.now(timezone('Asia/Seoul')).strftime(fmt)
        timestamp_str = '{0:s}'.format('[Timestamp: ' + cur_time + ']')
        tmp_str = timestamp_str + ' 원본 데이터 파일 목록'
        log_str += tmp_str + '\n'
        print(tmp_str)

        original_data_log_str = self.getOriginalDataLog()
        log_str += original_data_log_str + '\n'

        # Start making get_on, get_off, idle data
        cur_time = datetime.now(timezone('Asia/Seoul')).strftime(fmt)
        timestamp_str = '{0:s}'.format('[Timestamp: ' + cur_time + ']')
        tmp_str = timestamp_str + ' 승하차 데이터 가공 시작'
        log_str += tmp_str + '\n'
        print(tmp_str)

        self.makeGetOnOffData()

        # Get get_on data list
        cur_time = datetime.now(timezone('Asia/Seoul')).strftime(fmt)
        timestamp_str = '{0:s}'.format('[Timestamp: ' + cur_time + ']')
        tmp_str = timestamp_str + ' 승차(Get On) 데이터 파일 목록 및 사용된 원본 데이터 목록'
        log_str += tmp_str + '\n'
        print(tmp_str)

        get_on_log_str = self.getGetOnDataLog()
        log_str += get_on_log_str + '\n'

        # Get get_off data list
        cur_time = datetime.now(timezone('Asia/Seoul')).strftime(fmt)
        timestamp_str = '{0:s}'.format('[Timestamp: ' + cur_time + ']')
        tmp_str = timestamp_str + ' 하차(Get Off) 데이터 파일 목록 및 사용된 원본 데이터 목록'
        log_str += tmp_str + '\n'
        print(tmp_str)

        get_off_log_str = self.getGetOffDataLog()
        log_str += get_off_log_str + '\n'

        # Get Idle data list
        cur_time = datetime.now(timezone('Asia/Seoul')).strftime(fmt)
        timestamp_str = '{0:s}'.format('[Timestamp: ' + cur_time + ']')
        tmp_str = timestamp_str + ' 무관(Idle) 데이터 파일 목록 및 사용된 원본 데이터 목록'
        log_str += tmp_str + '\n'
        print(tmp_str)

        idle_log_str = self.getIdleDataLog()
        log_str += idle_log_str + '\n'

        # Start divide training, validation, test data
        cur_time = datetime.now(timezone('Asia/Seoul')).strftime(fmt)
        timestamp_str = '{0:s}'.format('[Timestamp: ' + cur_time + ']')
        tmp_str = timestamp_str + ' Training(80%)/Validation(10%)/Test(10%) 데이터 분할 시작'
        log_str += tmp_str + '\n'
        print(tmp_str)

        self.divideDataByRate()

        # Get train data list
        cur_time = datetime.now(timezone('Asia/Seoul')).strftime(fmt)
        timestamp_str = '{0:s}'.format('[Timestamp: ' + cur_time + ']')
        tmp_str = timestamp_str + ' Training(80%) 데이터 파일 목록'
        log_str += tmp_str + '\n'
        print(tmp_str)

        train_log_str = self.getTrainDataLog()
        log_str += train_log_str + '\n'

        # Get val data list
        cur_time = datetime.now(timezone('Asia/Seoul')).strftime(fmt)
        timestamp_str = '{0:s}'.format('[Timestamp: ' + cur_time + ']')
        tmp_str = timestamp_str + ' Validation(10%) 데이터 파일 목록'
        log_str += tmp_str + '\n'
        print(tmp_str)

        val_log_str = self.getValDataLog()
        log_str += val_log_str + '\n'

        # Get test data list
        cur_time = datetime.now(timezone('Asia/Seoul')).strftime(fmt)
        timestamp_str = '{0:s}'.format('[Timestamp: ' + cur_time + ']')
        tmp_str = timestamp_str + ' Test(10%) 데이터 파일 목록'
        log_str += tmp_str + '\n'
        print(tmp_str)

        test_log_str = self.getTestDataLog()
        log_str += test_log_str + '\n'

        # summary of data
        cur_time = datetime.now(timezone('Asia/Seoul')).strftime(fmt)
        timestamp_str = '{0:s}'.format('[Timestamp: ' + cur_time + ']')
        tmp_str = timestamp_str + ' 데이터 요약'
        log_str += tmp_str + '\n'
        print(tmp_str)

        tmp_str = '원본 데이터 JSON 파일 개수: {}'.format(str(self.original_num))
        log_str += tmp_str + '\n'
        print(tmp_str)

        tmp_str = '승차(Get On) 데이터 JSON 파일 개수: {}'.format(str(self.get_on_num))
        log_str += tmp_str + '\n'
        print(tmp_str)

        tmp_str = '하차(Get Off) 데이터 JSON 파일 개수: {}'.format(str(self.get_off_num))
        log_str += tmp_str + '\n'
        print(tmp_str)

        tmp_str = '무관(Idle) 데이터 JSON 파일 개수: {}'.format(str(self.idle_num))
        log_str += tmp_str + '\n'
        print(tmp_str)

        tmp_str = 'Training(80%) 데이터 JSON 파일 개수: {} (Get On: {}, Get Off: {}, Idle: {})'.format(
            self.train_num,
            self.train_get_on_num,
            self.train_get_off_num,
            self.train_idle_num
        )
        log_str += tmp_str + '\n'
        print(tmp_str)

        tmp_str = 'Validation(10%) 데이터 JSON 파일 개수: {} (Get On: {}, Get Off: {}, Idle: {})'.format(
            self.val_num,
            self.val_get_on_num,
            self.val_get_off_num,
            self.val_idle_num
        )
        log_str += tmp_str + '\n'
        print(tmp_str)

        tmp_str = 'Test(10%) 데이터 JSON 파일 개수: {} (Get On: {}, Get Off: {}, Idle: {})'.format(
            self.test_num,
            self.test_get_on_num,
            self.test_get_off_num,
            self.test_idle_num
        )
        log_str += tmp_str + '\n'
        print(tmp_str)

        cur_time = datetime.now(timezone('Asia/Seoul')).strftime(fmt)
        timestamp_str = '{0:s}'.format('[Timestamp: ' + cur_time + ']')
        tmp_str = timestamp_str + ' 데이터 가공 완료'
        log_str += tmp_str + '\n\n'
        print(tmp_str)

        return log_str

In [218]:
get_on_off_data = GetOnOffData2("/content/drive/Othercomputers/내 노트북/Forked_Models/Data_A/Label_A",
                                "/content/drive/Othercomputers/내 노트북/Forked_Models/승객 승하차 분류 유효성/Model 동작확인 및 C채널 적용 테스트/Apply_to_chC/getonoff/",
                                "/content/drive/Othercomputers/내 노트북/Forked_Models/승객 승하차 분류 유효성/Model 동작확인 및 C채널 적용 테스트/Apply_to_chC/dataset",(0.8, 0.1))

1


100%|██████████| 1/1 [00:00<00:00, 93.20it/s]


In [219]:
get_on_off_data.generateGetOnOffData()

[Timestamp: 2023-05-15 18:36:10 KST+0900] 원본 데이터 파일 목록
1. /content/drive/Othercomputers/내 노트북/Forked_Models/Data_A/Label_A/[district]attend_003A_000.json
2. /content/drive/Othercomputers/내 노트북/Forked_Models/Data_A/Label_A/[district]attend_003A_003.json
3. /content/drive/Othercomputers/내 노트북/Forked_Models/Data_A/Label_A/[district]attend_003A_006.json
4. /content/drive/Othercomputers/내 노트북/Forked_Models/Data_A/Label_A/[district]attend_003A_009.json
5. /content/drive/Othercomputers/내 노트북/Forked_Models/Data_A/Label_A/[district]attend_003A_012.json
6. /content/drive/Othercomputers/내 노트북/Forked_Models/Data_A/Label_A/[district]attend_003A_015.json
7. /content/drive/Othercomputers/내 노트북/Forked_Models/Data_A/Label_A/[district]attend_003A_018.json
8. /content/drive/Othercomputers/내 노트북/Forked_Models/Data_A/Label_A/[district]attend_003A_021.json
9. /content/drive/Othercomputers/내 노트북/Forked_Models/Data_A/Label_A/[district]attend_003A_024.json
10. /cont

  0%|          | 0/1 [00:00<?, ?it/s]

tf.Tensor(
[[[    0.83281     0.43519   0.0036458   -0.039815   -0.040625   -0.025926    0.010417     0.05463]
  [    0.83281     0.43519  -0.0015625   -0.040741   -0.040625   -0.025926    0.010417     0.05463]
  [    0.83281     0.43519    -0.00625   -0.031481   -0.040625   -0.025926    0.010417     0.05463]]], shape=(1, 3, 8), dtype=float32)
[2]
/content/drive/Othercomputers/내 노트북/Forked_Models/Data_A/Label_A/[district]attend_003A_162.json
tf.Tensor(
[[[    0.83281     0.43519  -0.0015625   -0.040741   -0.040625   -0.025926    0.010417     0.05463]
  [    0.83281     0.43519    -0.00625   -0.031481   -0.040625   -0.025926    0.010417     0.05463]
  [    0.83281     0.43519    -0.00625   -0.031481   -0.040625   -0.025926    0.010417     0.05463]]], shape=(1, 3, 8), dtype=float32)
[2]
/content/drive/Othercomputers/내 노트북/Forked_Models/Data_A/Label_A/[district]attend_003A_177.json
tf.Tensor(
[[[    0.83281     0.43519    -0.00625   -0.031481   -0.040625   -0.025926    0.010417 

100%|██████████| 1/1 [00:04<00:00,  4.11s/it]


[Timestamp: 2023-05-15 18:36:18 KST+0900] 승차(Get On) 데이터 파일 목록 및 사용된 원본 데이터 목록
[Timestamp: 2023-05-15 18:36:18 KST+0900] 하차(Get Off) 데이터 파일 목록 및 사용된 원본 데이터 목록
[Timestamp: 2023-05-15 18:36:18 KST+0900] 무관(Idle) 데이터 파일 목록 및 사용된 원본 데이터 목록
1. /content/drive/Othercomputers/내 노트북/Forked_Models/승객 승하차 분류 유효성/Model 동작확인 및 C채널 적용 테스트/Apply_to_chC/getonoff/idle/idle_1.json
	time_step: 1, original_data_path: /content/drive/Othercomputers/내 노트북/Forked_Models/Validation/Validation/_라벨_General_val_C/district_sample2/[district]night_1100C/[district]night_1100C_0.json, id: 1
	time_step: 2, original_data_path: /content/drive/Othercomputers/내 노트북/Forked_Models/Validation/Validation/_라벨_General_val_C/district_sample2/[district]night_1100C/[district]night_1100C_2.json, id: 1
	time_step: 3, original_data_path: /content/drive/Othercomputers/내 노트북/Forked_Models/Validation/Validation/_라벨_General_val_C/district_sample2/[district]night_1100C/[district]night_1100C_4.json, 

100%|██████████| 547/547 [00:00<00:00, 1682.52it/s]

[Timestamp: 2023-05-15 18:36:18 KST+0900] Training(80%) 데이터 파일 목록
1. /content/drive/Othercomputers/내 노트북/Forked_Models/승객 승하차 분류 유효성/Model 동작확인 및 C채널 적용 테스트/Apply_to_chC/dataset/training/idle_1.json
2. /content/drive/Othercomputers/내 노트북/Forked_Models/승객 승하차 분류 유효성/Model 동작확인 및 C채널 적용 테스트/Apply_to_chC/dataset/training/idle_2.json
3. /content/drive/Othercomputers/내 노트북/Forked_Models/승객 승하차 분류 유효성/Model 동작확인 및 C채널 적용 테스트/Apply_to_chC/dataset/training/idle_3.json
4. /content/drive/Othercomputers/내 노트북/Forked_Models/승객 승하차 분류 유효성/Model 동작확인 및 C채널 적용 테스트/Apply_to_chC/dataset/training/idle_4.json
5. /content/drive/Othercomputers/내 노트북/Forked_Models/승객 승하차 분류 유효성/Model 동작확인 및 C채널 적용 테스트/Apply_to_chC/dataset/training/idle_5.json
6. /content/drive/Othercomputers/내 노트북/Forked_Models/승객 승ᄒ

'[Timestamp: 2023-05-15 18:36:10 KST+0900] 원본 데이터 파일 목록\n1. /content/drive/Othercomputers/내 노트북/Forked_Models/Data_A/Label_A/[district]attend_003A_000.json\n2. /content/drive/Othercomputers/내 노트북/Forked_Models/Data_A/Label_A/[district]attend_003A_003.json\n3. /content/drive/Othercomputers/내 노트북/Forked_Models/Data_A/Label_A/[district]attend_003A_006.json\n4. /content/drive/Othercomputers/내 노트북/Forked_Models/Data_A/Label_A/[district]attend_003A_009.json\n5. /content/drive/Othercomputers/내 노트북/Forked_Models/Data_A/Label_A/[district]attend_003A_012.json\n6. /content/drive/Othercomputers/내 노트북/Forked_Models/Data_A/Label_A/[district]attend_003A_015.json\n7. /content/drive/Othercomputers/내 노트북/Forked_Models/Data_A/Label_A/[district]attend_003A_018.json\n8. /content/drive/Othercomputers/내 노트북/Forked_Models/Data_A/Label_A/[district]attend_003A_021.json\n9. /content/drive/Othercomputers/내 노트북/Forked_Models/Data_A/Label_A/[district]attend_003A_024.json

# Evaluation(테스트데이터 셋에 대한 적용이므로, Evaluation이 불가능)

In [ ]:
#%cd "/content/drive/Othercomputers/내 노트북/Forked_Models/승객 승하차 분류 유효성/Model 동작확인 및 C채널 적용 테스트/Apply_to_chC"

/content/drive/Othercomputers/내 노트북/Forked_Models/승객 승하차 분류 유효성/Apply_to_chC


In [ ]:
#!python "evaluate.py"

# Make Video


In [220]:
import json

pt = "/content/drive/Othercomputers/내 노트북/Forked_Models/Data_A/Label_A"  #프레임별 json 파일이 들어있는 폴더 지정
file_list = sorted(os.listdir(pt))

# .json 확장자를 가진 파일 리스트 생성
js_file_list = []
for file_name in file_list:
    # 파일 이름과 확장자 분리
    name, ext = os.path.splitext(file_name)
    # 확장자가 .json인 파일 이름을 리스트에 추가
    if ext == ".json":
        js_file_list.append(file_name)

if len(js_file_list) == len(det_list):
  for i in range(len(det_list)):
    # JSON 파일 열기
    temp_file_path = pt + "/" + js_file_list[i]
    with open(temp_file_path, "r") as f:
      dt = json.load(f)      # JSON 데이터 읽어오기
      
      k = []
      print(len(dt["annotations"]))
      for j in range(len(dt["annotations"])):
        if (dt["annotations"][j]["get_on"] == True) & (dt["annotations"][j]["get_on"] == False):
          k.append([0])
        elif (dt["annotations"][j]["get_on"] == False) & (dt["annotations"][j]["get_on"] == True):
          k.append([1])
        else:
          k.append([2])
      print(k)
      print(det_list[i])
      if len(k) != 0:
        det_list[i] = tf.concat([det_list[i],tf.convert_to_tensor(k)], axis = 1)
        
print(det_list[80][0,57])



0
[]
tensor([], size=(0, 6))
0
[]
tensor([], size=(0, 6))
0
[]
tensor([], size=(0, 6))
0
[]
tensor([], size=(0, 6))
0
[]
tensor([], size=(0, 6))
0
[]
tensor([], size=(0, 6))
0
[]
tensor([], size=(0, 6))
0
[]
tensor([], size=(0, 6))
0
[]
tensor([], size=(0, 6))
0
[]
tensor([], size=(0, 6))
0
[]
tensor([], size=(0, 6))
0
[]
tensor([], size=(0, 6))
0
[]
tensor([], size=(0, 6))
0
[]
tensor([], size=(0, 6))
0
[]
tensor([], size=(0, 6))
0
[]
tensor([], size=(0, 6))
0
[]
tensor([], size=(0, 6))
0
[]
tensor([], size=(0, 6))
0
[]
tensor([], size=(0, 6))
0
[]
tensor([], size=(0, 6))
0
[]
tensor([], size=(0, 6))
0
[]
tensor([], size=(0, 6))
0
[]
tensor([], size=(0, 6))
0
[]
tensor([], size=(0, 6))
0
[]
tensor([], size=(0, 6))
0
[]
tensor([], size=(0, 6))
1
[[2]]
tensor([[1.82400e+03, 3.94000e+02, 1.91900e+03, 7.40000e+02, 2.41847e-01, 0.00000e+00, 1.08064e+03, 2.74171e+02, 6.76752e-02, 1.08157e+03, 2.68970e+02, 2.45136e-02, 1.07820e+03, 2.68695e+02, 8.66484e-02, 1.07292e+03, 2.66900e+02, 4.41628e

In [223]:
def scale_coords2(img1_shape, coords, img0_shape, ratio_pad=None):
    #print("ddd")
    # Rescale coords (xyxy) from img1_shape to img0_shape
    if ratio_pad is None:  # calculate from img0_shape
        gain = min(img1_shape[0] / img0_shape[0], img1_shape[1] / img0_shape[1])  # gain  = old / new
        pad = (img1_shape[1] - img0_shape[1] * gain) / 2, (img1_shape[0] - img0_shape[0] * gain) / 2  # wh padding
        #print("ddd")
    else:
        gain = ratio_pad[0][0]
        pad = ratio_pad[1]
     
    coords1 = tf.gather(coords, [0, 2], axis=1).numpy()-pad[0]  # x padding
    coords2 = tf.gather(coords, [1, 3], axis=1).numpy()-pad[1]  # y padding
    q=len(coords1[:,0])
    coords = np.concatenate((tf.reshape(coords1[:,0],[q,1]),tf.reshape(coords2[:,0],[q,1]),tf.reshape(coords1[:,1],[q,1]),tf.reshape(coords2[:,1],[q,1])),axis=1)
    coords[:, :4] /= gain
    clip_coords(torch.Tensor(coords), img0_shape)
    return torch.Tensor(coords)

def clip_coords(boxes, img_shape):
    # Clip bounding xyxy bounding boxes to image shape (height, width)
    boxes[:, 0].clamp_(0, img_shape[1])  # x1
    boxes[:, 1].clamp_(0, img_shape[0])  # y1
    boxes[:, 2].clamp_(0, img_shape[1])  # x2
    boxes[:, 3].clamp_(0, img_shape[0])  # y2

In [237]:
# 비디오 생성 함수
@torch.no_grad()
def gen_vid(
        det_list,
        source='/content/drive/Othercomputers/내 노트북/Forked_Models/Data_A/Image_A',
        yolo_weights= 'yolov5m.pt',  # model.pt path(s),
        strong_sort_weights='osnet_x0_25_msmt17.pt',  # model.pt path,
        config_strongsort='/content/drive/Othercomputers/내 노트북/Forked_Models/Yolov7_StrongSORT_OSNet/strong_sort/configs/strong_sort.yaml',
        imgsz=(1920, 1080),  # inference size (height, width)
        conf_thres=0.15,  # confidence threshold
        iou_thres=0.45,  # NMS IOU threshold
        max_det=1000,  # maximum detections per image
        device="cpu",  # cuda device, i.e. 0 or 0,1,2,3 or cpu
        show_vid=False,  # show results
        save_txt=False,  # save results to *.txt
        save_conf=False,  # save confidences in --save-txt labels
        save_crop=False,  # save cropped prediction boxes
        save_vid=True,  # save confidences in --save-txt labels
        nosave=False,  # do not save images/videos
        classes=0,  # filter by class: --class 0, or --class 0 2 3
        agnostic_nms=False,  # class-agnostic NMS
        augment=False,  # augmented inference
        visualize=False,  # visualize features
        update=False,  # update all models
        project='/content/drive/Othercomputers/내 노트북/Forked_Models/Data_A',  # save results to project/name
        name='exp',  # save results to project/name
        exist_ok=False,  # existing project/name ok, do not increment
        line_thickness=3,  # bounding box thickness (pixels)
        hide_labels=False,  # hide labels
        hide_conf=False,  # hide confidences
        hide_class=False,  # hide IDs
        half=False,  # use FP16 half-precision inference
        dnn=False,  # use OpenCV DNN for ONNX inference
):
    source = str(source)
    save_img = not nosave and not source.endswith('.txt')  # save inference images
    is_file = Path(source).suffix[1:] in (VID_FORMATS)
    is_url = source.lower().startswith(('rtsp://', 'rtmp://', 'http://', 'https://'))
    webcam = source.isnumeric() or source.endswith('.txt') or (is_url and not is_file)
    if is_url and is_file:
        source = check_file(source)  # download

    # Directories
    if not isinstance(yolo_weights, list):  # single yolo model
        exp_name = pathlib.Path(yolo_weights).stem
    elif type(yolo_weights) is list and len(yolo_weights) == 1:  # single models after --yolo_weights
        exp_name = pathlib.Path(yolo_weights[0]).stem
        yolo_weights = Path(yolo_weights[0])
    else:  # multiple models after --yolo_weights
        exp_name = 'ensemble'
    exp_name = name if name else exp_name + "_" + strong_sort_weights.stem
    save_dir = increment_path(Path(project) / exp_name, exist_ok=exist_ok)  # increment run
    save_dir = Path(save_dir)
    (save_dir + '/tracks' if save_txt else save_dir).mkdir(parents=True, exist_ok=True)  # make dir

    # # Load model
    # device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
    # print(device)

    # pathlib.Path(WEIGHTS).mkdir(parents=True, exist_ok=True)
    model = loading_yolov7_model(Path("/content/drive/Othercomputers/내 노트북/Forked_Models/Yolov7_StrongSORT_OSNet/yolov7/yolov7-w6-pose.pt"), device)  # load FP32 model
    names, = model.names,
    stride = model.stride.max().cpu().numpy()  # model stride
    imgsz = check_img_size(imgsz[0], s=stride)  # check image size

    # Dataloader
    if webcam:
        show_vid = check_imshow()
        cudnn.benchmark = True  # set True to speed up constant image size inference
        dataset = LoadStreams(source, img_size=imgsz, stride=stride)
        nr_sources = 1
    else:
        dataset = LoadImages(source, img_size=imgsz, stride=stride)
        nr_sources = 1
    vid_path, vid_writer, txt_path = [None] * nr_sources, [None] * nr_sources, [None] * nr_sources

    # # initialize StrongSORT
    # cfg = get_config()
    # cfg.merge_from_file(config_strongsort)

    # # Create as many strong sort instances as there are video sources
    # strongsort_list = []
    # for i in range(nr_sources):
    #     strongsort_list.append(
    #         StrongSORT(
    #             strong_sort_weights,
    #             device,
    #             half,
    #             max_dist=cfg.STRONGSORT.MAX_DIST,
    #             max_iou_distance=cfg.STRONGSORT.MAX_IOU_DISTANCE,
    #             max_age=cfg.STRONGSORT.MAX_AGE,
    #             n_init=cfg.STRONGSORT.N_INIT,
    #             nn_budget=cfg.STRONGSORT.NN_BUDGET,
    #             mc_lambda=cfg.STRONGSORT.MC_LAMBDA,
    #             ema_alpha=cfg.STRONGSORT.EMA_ALPHA,

    #         )
    #     )
    #     strongsort_list[i].model.warmup()
    outputs = [None] * nr_sources
    
    colors = [[random.randint(0, 255) for _ in range(3)] for _ in names]

    # Run tracking
    dt, seen = [0.0, 0.0, 0.0, 0.0], 0
    curr_frames, prev_frames = [None] * nr_sources, [None] * nr_sources
    for frame_idx, (path, im, im0s, vid_cap) in enumerate(dataset):
        s = ''
        # t1 = time_synchronized()
        im = torch.from_numpy(im).to(device)
        im = im.half() if half else im.float()  # uint8 to fp16/32
        im /= 255.0  # 0 - 255 to 0.0 - 1.0
        if len(im.shape) == 3:
            im = im[None]  # expand for batch dim
        # t2 = time_synchronized()
        # dt[0] += t2 - t1

        # Inference
        visualize = increment_path(save_dir / Path(path[0]).stem, mkdir=True) if visualize else False
        # pred, im2 = model(im)
        # t3 = time_synchronized()
        # dt[1] += t3 - t2

        # Apply NMS
        # pred = non_max_suppression_kpt(pred,
        #                                conf_thres,  # Confidence Threshold
        #                                iou_thres,  # IoU Threshold
        #                                nc=model.yaml['nc'],  # Number of Classes
        #                                nkpt=model.yaml['nkpt'],  # Number of Keypoints
        #                                kpt_label=True)
        
        # with torch.no_grad():
        #   pred_kpt = output_to_keypoint(pred)
        
        # dt[2] += time_synchronized() - t3

        # Process detections
        for i, pose in enumerate([det_list]):  # detections per image
            det = det_list[seen].numpy()
            seen += 1
            if webcam:  # nr_sources >= 1
                p, im0, _ = path[i], im0s[i].copy(), dataset.count
                p = Path(p)  # to Path
                s += f'{i}: '
                txt_file_name = p.name
                save_path = str(save_dir / p.name)  # im.jpg, vid.mp4, ...
            else:
                p, im0, _ = path, im0s.copy(), getattr(dataset, 'frame', 0)
                p = Path(p)  # to Path
                # video file
                if source.endswith(VID_FORMATS):
                    txt_file_name = p.stem
                    save_path = str(save_dir / p.name)  # im.jpg, vid.mp4, ...
                # folder with imgs
                else:
                    txt_file_name = p.parent.name  # get folder name containing current img
                    save_path = str(save_dir / p.parent.name)  # im.jpg, vid.mp4, ...
            #print(len(curr_frames))
            curr_frames[i] = im0

            txt_path = str(str(save_dir) + '/tracks' + txt_file_name)  # im.txt
            s += '%gx%g ' % im.shape[2:]  # print string
            imc = im0.copy() if save_crop else im0  # for save_crop

            # if cfg.STRONGSORT.ECC:  # camera motion compensation
            #     strongsort_list[i].tracker.camera_update(prev_frames[i], curr_frames[i])
            
            #print(type(pred[0]))

            #return det    # 디버그 용
            if det is not None and len(det):
                # Rescale boxes from img_size to im0 size
                print(len(det[0]))
                print(seen)
                print(len(im0))
                det[:, :4] = scale_coords2(im.shape[2:], det[:, :4], im0.shape).round()

                # Print results
                for c in set(det[:, -2]):
                    n = (det[:, -2] == c).sum()  # detections per class
                    #print(names)
                    s += f"{n} {names[int(c)]}{'s' * (n > 1)}, "  # add to string

                xywhs = xyxy2xywh(det[:, 0:4])
                confs = det[:, 4]
                clss = det[:, 5]

                # pass detections to strongsort
                # t4 = time_synchronized()
                #outputs[i] = strongsort_list[i].update(xywhs.cpu(), confs.cpu(), clss.cpu(), im0)
                outputs[i] = tf.concat([det[:, :6],det[:, 57:]], axis = 1) # 의도분석 결과 합쳐지면 이 코드 사용하기*******************************************************
                #outputs[i] = det[:, :6]
                # t5 = time_synchronized()
                # dt[3] += t5 - t4

                # draw boxes for visualization
                if len(outputs[i]) > 0:
                    for j, (output, conf) in enumerate(zip(outputs[i], confs)):
                        #print(output)
                        bboxes = output[0:4]
                        id = output[4]
                        cls = output[5]
                        intent = output[6]                     # 의도분석 결과 합쳐지면 이 코드 사용하기*******************************************************
                        #print(output[6])

                        if save_txt:
                            # to MOT format
                            bbox_left = output[0]
                            bbox_top = output[1]
                            bbox_w = output[2] - output[0]
                            bbox_h = output[3] - output[1]
                            # Write MOT compliant results to file
                            with open(txt_path + '.txt', 'a') as f:
                                f.write(('%g ' * 10 + '\n') % (frame_idx + 1, id, bbox_left,  # MOT format
                                                               bbox_top, bbox_w, bbox_h, -1, -1, -1, i))

                        if save_vid or save_crop or show_vid:  # Add bbox to image
                            #c = int(cls)  # integer class
                            #print("a")
                            c = 0
                            id = int(id)  # integer id
                            label = None if hide_labels else (f'{id} {names[c]}' if hide_conf else \
                                (f'{id} {conf:.2f}' if hide_class else f'{id} {names[c]} {conf:.2f}'))
                            plot_one_box(bboxes, im0, label=label, color=colors[c], line_thickness=2)
                            #print(bboxes)
                            #print(im0)
                            if save_crop:
                                txt_file_name = txt_file_name if (isinstance(path, list) and len(path) > 1) else ''
                                save_one_box(bboxes, imc, file=save_dir + '/crops' / txt_file_name / names[c] / f'{id}' / f'{p.stem}.jpg', BGR=True)


                        if save_vid or save_crop or show_vid:  # Add bbox to image  (의도분석 결과 박스)*******************************************************************
                            #c = int(cls)  # integer class
                            c = 0
                            intent = int(intent)  # integer id
                            if intent == 0:
                              intent_c = [50,0,0,50]
                            elif intent == 2: # 나중에 1로 바꿔주기******************************************************************************************
                              intent_c = [150,0,0,50]
                            else:
                              continue
                            print("kkkkk")  
                            plot_one_box(bboxes, im0, label=label, color=intent_c, line_thickness=-1)
                            if save_crop:
                                txt_file_name = txt_file_name if (isinstance(path, list) and len(path) > 1) else ''
                                save_one_box(bboxes, imc, file=save_dir + '/crops' / txt_file_name / names[c] / f'{id}' / f'{p.stem}.jpg', BGR=True)



                print(f'{s}Done.')

            else:
                # strongsort_list[i].increment_ages()
                print('No detections')

            # Stream results
            if show_vid:
                cv2.imshow(str(p), im0)
                cv2.waitKey(1)  # 1 millisecond

            # Save results (image with detections)
            if save_vid:
                if vid_path[i] != save_path:  # new video
                    vid_path[i] = save_path
                    if isinstance(vid_writer[i], cv2.VideoWriter):
                        vid_writer[i].release()  # release previous video writer
                    if vid_cap:  # video
                        fps = vid_cap.get(cv2.CAP_PROP_FPS)
                        w = int(vid_cap.get(cv2.CAP_PROP_FRAME_WIDTH))
                        h = int(vid_cap.get(cv2.CAP_PROP_FRAME_HEIGHT))
                    else:  # stream
                        fps, w, h = 30, im0.shape[1], im0.shape[0]
                    save_path = str(Path(save_path).with_suffix('.mp4'))  # force *.mp4 suffix on results videos
                    vid_writer[i] = cv2.VideoWriter(save_path, cv2.VideoWriter_fourcc(*'mp4v'), fps, (w, h))
                vid_writer[i].write(im0)

            prev_frames[i] = curr_frames[i]

    # Print results
    t = tuple(x / seen * 1E3 for x in dt)  # speeds per image
    print(f'Speed: %.1fms pre-process, %.1fms inference, %.1fms NMS, %.1fms strong sort update per image at shape {(1, 3, imgsz, imgsz)}' % t)
    if save_txt or save_vid:
        s = f"\n{len(list(save_dir.glob('track/*.txt')))} tracks saved to {save_dir / 'track'}" if save_txt else ''
        print(f"Results saved to {colorstr('bold', save_dir)}{s}")
    if update:
        strip_optimizer(yolo_weights)  # update model (to fix SourceChangeWarning)
    
    return()

In [238]:
gen_vid(det_list)

Loading model: /content/drive/Othercomputers/내 노트북/Forked_Models/Yolov7_StrongSORT_OSNet/yolov7/yolov7-w6-pose.pt
No detections
No detections
No detections
No detections
No detections
No detections
No detections
No detections
No detections
No detections
No detections
No detections
No detections
No detections
No detections
No detections
No detections
No detections
No detections
No detections
No detections
No detections
No detections
No detections
No detections
No detections
58
27
1080


<ipython-input-237-0343d4817459>:182: DeprecationWarning: In future, it will be an error for 'np.bool_' scalars to be interpreted as an index
  s += f"{n} {names[int(c)]}{'s' * (n > 1)}, "  # add to string


kkkkk
1088x1920 1 person, Done.
No detections
No detections
No detections
No detections
No detections
No detections
58
34
1080
kkkkk
1088x1920 1 person, Done.
No detections
No detections
No detections
No detections
No detections
No detections
No detections
No detections
No detections
No detections
No detections
58
46
1080
kkkkk
kkkkk
kkkkk
1088x1920 3 persons, Done.
No detections
No detections
58
49
1080
kkkkk
1088x1920 1 person, Done.
No detections
58
51
1080
kkkkk
1088x1920 1 person, Done.
58
52
1080
kkkkk
1088x1920 1 person, Done.
58
53
1080
kkkkk
1088x1920 1 person, Done.
58
54
1080
kkkkk
kkkkk
1088x1920 2 persons, Done.
58
55
1080
kkkkk
1088x1920 1 person, Done.
No detections
No detections
58
58
1080
kkkkk
1088x1920 1 person, Done.
58
59
1080
kkkkk
kkkkk
1088x1920 2 persons, Done.
58
60
1080
kkkkk
1088x1920 1 person, Done.
58
61
1080
kkkkk
1088x1920 1 person, Done.
58
62
1080
kkkkk
1088x1920 1 person, Done.
58
63
1080
kkkkk
1088x1920 1 person, Done.
58
64
1080
kkkkk
1088x1920 1 pe

()

In [221]:
inn = tf.constant([0, 2])
len(det_list[80][0])


58

In [186]:
t = tf.reshape(tf.gather(det_list[80][:, :4], [1, 3], axis=1)[0],[2,1])
t

<tf.Tensor: shape=(1, 2), dtype=int32, numpy=array([[101, 499]], dtype=int32)>

In [183]:
t = tf.gather(det_list[80][:, :4], [1, 3], axis=1)[0]
t

<tf.Tensor: shape=(2,), dtype=int32, numpy=array([101, 499], dtype=int32)>

In [190]:
t = tf.reshape(tf.gather(det_list[80][:, :4], [1, 3], axis=1)[0],[2,1])
t
t1 = tf.reshape(tf.gather(det_list[80][:, :4], [1, 3], axis=1)[1],[2,1])
np.concatenate((t,t1),axis=1)

array([[101, 370],
       [499, 787]], dtype=int32)

In [66]:
type(tf.convert_to_tensor(det_list[80]))


tensorflow.python.framework.ops.EagerTensor